In [1]:
from flightdata import Flight
from flightanalysis import Section, FlightLine
from flightplotting.plots import meshes, tiptrace, create_3d_plot
from flightplotting.model import OBJ
from geometry import Transformation, Quaternion
import plotly.graph_objects as go
import plotly.express as px
from plotly.subplots import make_subplots
import numpy as np
import pandas as pd
from geometry import Point, Points

flight = Flight.from_csv("../../data/logs/00000136.csv")
sec = Section.from_flight(flight, FlightLine.from_covariance(flight))

flown_vertical_8 = sec.subset(102,147)

/home/tom/source/PyFlightCoach/geometry/geometry/points.py:103: RuntimeWarning: invalid value encountered in true_divide
  return Points(self.data / other[:, np.newaxis])


In [2]:


obj = OBJ.from_obj_file('../../data/models/ColdDraftF3APlane.obj').transform(
    Transformation(
        Point(0.75, 0, 0),
        Quaternion.from_euler(Point(np.pi, 0, -np.pi/2))
    )
)

fig = create_3d_plot(tiptrace(flown_vertical_8, 10.0) + meshes(obj.scale(10.0) , 40, flown_vertical_8))
fig.update_layout(width=400, height=400)
fig.show()

In [3]:


px.line(flown_vertical_8.brvel).update_layout(width=1000)



In [34]:

generated_vertical_8 = pd.DataFrame.from_records(
        [[0.0, 0.0, 0.0,      "elm1_entry_line"] for i in range(20)] +
        [[1.5, 0.0, 0.0,      "elm2_half_roll"] for i in range(20)] +
        [[0.0, -0.5, 0.0,     "elm3_outside_loop"] for i in range(20)] +
        [[0.0, 0.5, 0.0,      "elm4_inside_loop"] for i in range(20)] +
        [[-1.5, 0.0, 0.0,     "elm5_half_roll"] for i in range(20)] +
        [[0.0, 0.0, 0.0,      "elm6_exit_line"] for i in range(20)]
    ,
    columns="roll_rate,pitch_rate,yaw_rate,element".split(",")
)

px.line(generated_vertical_8, y="roll_rate,pitch_rate,yaw_rate".split(",")).update_layout(width=1000)


In [38]:
from scipy.spatial.distance import euclidean
from fastdtw import fastdtw
import pandas as pd
x = generated_vertical_8.iloc[:, [0, 1, 2]].to_numpy()
y = flown_vertical_8.brvel.to_numpy()

distance, path = fastdtw(x, y, dist=euclidean)
segments = flown_vertical_8.data.reset_index().join(
    pd.DataFrame(path, columns="generated,flight".split(",")).set_index(
        "flight").join(generated_vertical_8.element, on="generated")
)



In [60]:
fig=None
fig = px.line_3d(segments, x="x", y="y", z="z", color="element")

fig.update_traces(line=dict(width=5))

fig.update_layout(
            margin=dict(l=0, r=0, t=0, b=0),
            scene=dict(aspectmode='data'),
            width=700, height=700
        )

tt = tiptrace(flown_vertical_8, 10)
fig.add_trace(tt[0])
fig.add_trace(tt[1])


In [1]:
import numpy as np

generated_loop = pd.DataFrame.from_records(
    np.row_stack([
        np.zeros((20,3)),
        np.zeros((20,3))
    ])
)


#        [[0.0, 0.0, 0.0,      "elm1_entry_line"] for i in range(20)] +
#        [[0.0, -0.5, 0.0,      "elm2_45_push"] for i in range(20)] +
#        [[0.0, 0.0, 0.0,     "elm3_45_line"] for i in range(20)] +
#        [[0.0, -0.5, 0.0,      "elm4_1/8_outside_loop"] for i in range(20)] +
#        [np.full(), np.linspace(-0.5, 0.5, 20), 0.0,     "elm5_half_roll"] +
#        [[0.0, 0.0, 0.0,      "elm6_exit_line"] for i in range(20)]
#    ,
#    columns="roll_rate,pitch_rate,yaw_rate,element".split(",")
#)

px.line(generated_vertical_8, y="roll_rate,pitch_rate,yaw_rate".split(",")).update_layout(width=1000)

NameError: name 'pd' is not defined

In [4]:
import plotly.express as px
xs = np.linspace(0,np.pi, 20)
ys = np.sin(np.linspace(0,np.pi, 20))
px.scatter(x=xs,y=[np.sin(np.linspace(0,np.pi, 20)), np.cos(np.linspace(0,np.pi, 20))])